In [3]:
exp_index = 0
experiments = {}

# Imports

In [4]:
import pandas as pd
from sklearn.model_selection import train_test_split, KFold, RepeatedKFold, RepeatedStratifiedKFold, StratifiedKFold
from sklearn import set_config

from sklearn.linear_model import LogisticRegression, RidgeClassifier, RidgeClassifierCV, SGDClassifier, PassiveAggressiveClassifier, Perceptron
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier, ExtraTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier, ExtraTreesClassifier, BaggingClassifier, HistGradientBoostingClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier
from sklearn.svm import SVC, NuSVC, LinearSVC
from sklearn.naive_bayes import GaussianNB, BernoulliNB, ComplementNB, MultinomialNB
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis, LinearDiscriminantAnalysis
from sklearn.neural_network import MLPClassifier
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.calibration import CalibratedClassifierCV
from sklearn.dummy import DummyClassifier

from sklearn.preprocessing import StandardScaler, PowerTransformer, QuantileTransformer, RobustScaler, MinMaxScaler
from sklearn.decomposition import PCA, KernelPCA
from sklearn.feature_selection import SelectKBest, SelectFromModel, f_regression
from sklearn.feature_selection import SequentialFeatureSelector
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import PolynomialFeatures
from sklearn.base import TransformerMixin, BaseEstimator
from sklearn.kernel_approximation import Nystroem, RBFSampler
from sklearn.metrics import roc_auc_score, accuracy_score, f1_score, precision_score, recall_score
from sklearn.model_selection import cross_validate, cross_val_score, cross_val_predict

import numpy as np
import time
import optuna

# pandas deactivate future warnings
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter(action='ignore', category=UserWarning)
warnings.simplefilter(action='ignore', category=RuntimeWarning)

In [5]:
SUBMIT = True
USE_ORIGINAL = True
SEED = 15
SAMPLE = 1
TARGET = 'target'
# cv = KFold(n_splits=5, shuffle=True, random_state=SEED)
cv = RepeatedStratifiedKFold(n_splits=10, n_repeats=10, random_state=SEED)

train = pd.read_csv('dataset/train.csv')
test = pd.read_csv('dataset/test.csv')
orig = pd.read_csv('dataset/kindey stone urine analysis.csv')

for i, X in enumerate([train, test, orig]):
    if 'id' in X.columns:
        X.drop(['id'], axis=1, inplace=True)

# Define test set with original data
if not SUBMIT:
    train, test = train_test_split(train, test_size=0.2, random_state=SEED) 

# Add original data to training set
if USE_ORIGINAL:
    train = pd.concat([train, orig], axis=0)
    train.reset_index(inplace=True, drop=True)

# Sampling for faster training
if SAMPLE < 1:
    train = train.sample(frac=SAMPLE, random_state=SEED)

# set training data
X_train = train.copy()
y_train = X_train.pop(TARGET)
X_test = test.copy()

if not SUBMIT:
    y_test = X_test.pop(TARGET)
else:
    y_test = None

# print shapes
print(f'Train shape: {train.shape}, Test shape: {test.shape}, Original shape: {orig.shape}')

Train shape: (493, 7), Test shape: (276, 6), Original shape: (79, 7)


# Pipeline

In [6]:
classifiers = {
    # 'LogisticRegression1': LogisticRegression(random_state=SEED, max_iter=10000),
    'LogisticRegression2': LogisticRegression(random_state=SEED, penalty='l1', solver='liblinear', max_iter=10000, C=0.02),
    # 'KNeighborsClassifier': KNeighborsClassifier(),
    # 'KNeighborsClassifier15': KNeighborsClassifier(n_neighbors=15),
    # 'DecisionTreeClassifier': DecisionTreeClassifier(random_state=SEED),
    # 'RandomForestClassifier': RandomForestClassifier(random_state=SEED),
    # 'AdaBoostClassifier': AdaBoostClassifier(random_state=SEED),
    # 'GradientBoostingClassifier': GradientBoostingClassifier(random_state=SEED),
    # 'XGBClassifier': XGBClassifier(random_state=SEED),
    # 'LGBMClassifier1': LGBMClassifier(random_state=SEED),
    # 'LGBMClassifier2': LGBMClassifier(boosting_type='gbdt', max_depth=1, learning_rate=0.33, random_state=SEED),
    # 'CatBoostClassifier': CatBoostClassifier(random_state=SEED, verbose=0),
    # 'ExtraTreesClassifier': ExtraTreesClassifier(random_state=SEED),
    # 'SVC1': SVC(random_state=SEED, probability=True),
    # 'SVC2': SVC(random_state=SEED, probability=True, kernel='linear', C=0.02),
    # 'NuSVC': NuSVC(random_state=SEED, probability=True),
    # 'LinearSVC': LinearSVC(random_state=SEED, max_iter=100000),
    'GaussianNB': GaussianNB(),
    # 'QuadraticDiscriminantAnalysis': QuadraticDiscriminantAnalysis(),
    # 'MLPClassifier': MLPClassifier(random_state=SEED, max_iter=1000),
    # 'RidgeClassifier': RidgeClassifier(random_state=SEED),
    # 'RidgeClassifierCV': RidgeClassifierCV(),
    # 'SGDClassifier': SGDClassifier(random_state=SEED),
    # 'PassiveAggressiveClassifier': PassiveAggressiveClassifier(random_state=SEED),
    # 'Perceptron': Perceptron(random_state=SEED),
    # 'LinearDiscriminantAnalysis': LinearDiscriminantAnalysis(),
    'GaussianProcessClassifier': GaussianProcessClassifier(random_state=SEED),
    # 'BaggingClassifier': BaggingClassifier(random_state=SEED),
    # 'HistGradientBoostingClassifier': HistGradientBoostingClassifier(random_state=SEED),
    'BernoulliNB': BernoulliNB(),
    # 'ComplementNB': ComplementNB(),
    # 'MultinomialNB': MultinomialNB(),
    # 'DummyClassifier': DummyClassifier(random_state=SEED),
    # 'CalibratedClassifierCV_LR': CalibratedClassifierCV(estimator=LogisticRegression(random_state=SEED, max_iter=10000), cv=cv),
    # 'CalibratedClassifierCV_Ridge': CalibratedClassifierCV(estimator=RidgeClassifier(random_state=SEED), cv=cv),
    # 'CalibratedClassifierCV_SGD': CalibratedClassifierCV(estimator=SGDClassifier(random_state=SEED), cv=cv),
    # 'CalibratedClassifierCV_PA': CalibratedClassifierCV(estimator=PassiveAggressiveClassifier(random_state=SEED), cv=cv),
    # 'CalibratedClassifierCV_Perceptron': CalibratedClassifierCV(estimator=Perceptron(random_state=SEED), cv=cv),
    'CalibratedClassifierCV_ET': CalibratedClassifierCV(estimator=ExtraTreesClassifier(random_state=SEED), cv=cv),

    # 'XGBClassifier1': XGBClassifier(**xgb_params1),
    # 'XGBClassifier2': XGBClassifier(**xgb_params2),
    'DummyClassifier': DummyClassifier(random_state=SEED),
}

# Feature engineering
class FeatureEngineering(TransformerMixin, BaseEstimator):

    def __init__(self, level=0) -> None:
        self.level = level

    def fit(self, X, y=None):
        return self
    
    def transform(self, X, y=None):
        """ Add new features to the dataset"""
        X = X.copy()

        # Sum of features
        if self.level >= 1:

            # Ion product of calcium and urea
            X["ion_product"] = X["calc"] * X["urea"]

            # Calcium-to-urea ratio
            X["calcium_to_urea_ratio"] = X["calc"] / X["urea"]

            # Electrolyte balance
            X["electrolyte_balance"] = X["cond"] / (10 ** (-X["ph"]))

            # Osmolality-to-specific gravity ratio
            X["osmolality_to_sg_ratio"] = X["osmo"] / X["gravity"]
            
            ## Add Feature engineering part 
            # The product of osmolarity and density is created as a new property
            X['osmo_density'] = X['osmo'] * X['gravity']
            
            # Converting pH column to categorical variable
            X['pH_cat'] = pd.cut(X['ph'], bins=[0, 4.5, 6.5, 8.5, 14], labels=['sangat acidic' , 'acidic', 'neutral', 'basic' ])
            dummies = pd.get_dummies(X['pH_cat'])
            X = pd.concat([X, dummies], axis=1)
            
            # Deleting columns using dummy variables.
            # X.drop(['pH_cat', 'sangat acidic' , 'basic','neutral','ph'], axis=1, inplace=True)
            X.drop(['pH_cat'], axis=1, inplace=True)

        self.feature_names_out_ = X.columns.tolist()
        return X
    
    def get_feature_names_out(self):
        return self.feature_names_out_
    
# Transformer that will keep only the selected features
class FeatureSelector(TransformerMixin, BaseEstimator):
    def __init__(self, feature_names):
        self.feature_names = feature_names

    def fit(self, X, y=None):
        return self

    def transform(self, X, y=None):
        return X[self.feature_names]

    def get_feature_names_out(self):
        return self.feature_names

def get_pipeline(classifier, model_name):
    pipeline = make_pipeline(
        # Feature selection
        # FeatureSelector(feature_names=['calc', 'cond']),  #'gravity', 'ph', 'osmo', 'cond', 'urea', 'calc', 'target'

        # FeatureEngineering(level=1),
        # ClusterFeatures(n_clusters=7, random_state=SEED, ohe=True),
        # PolynomialFeatures(degree=2, include_bias=False, interaction_only=True),

        # StandardScaler(),
        PowerTransformer(method='yeo-johnson', standardize=True, copy=True),
        # PowerTransformer(method='box-cox', standardize=True, copy=True),
        # QuantileTransformer(output_distribution='normal', random_state=SEED),
        # RobustScaler(quantile_range=(5.0, 95.0), with_centering=True, with_scaling=True),
        # MinMaxScaler(feature_range=(0, 1)),

        # PCA(n_components=3, random_state=SEED),
        # KernelPCA(n_components=2, kernel='rbf', random_state=SEED),

        # SelectKBest(score_func=f_regression, k=30),
        # SelectFromModel(regressor, max_features=20),
        # SequentialFeatureSelector(classifier, n_features_to_select=3),

        # Kernel approximation
        Nystroem(kernel='rbf', n_components=3, random_state=SEED),
        # RBFSampler(gamma=1.0, n_components=100, random_state=SEED),

        classifier,
        # TransformedTargetRegressor(regressor=regressor, transformer=QuantileTransformer(output_distribution='normal', random_state=SEED))
    )
    return pipeline

In [12]:
set_config(transform_output="pandas")  # set to pandas

exp_index += 1
print(f'Experiment {exp_index}: {len(classifiers)} models')
print('Model name'.ljust(30), '|', 'ROC AUC'.rjust(10),'|', 'roc std'.rjust(10), '|', 'Accuracy'.rjust(10), '|', 'F1'.rjust(10), '|', 'Precision'.rjust(10), '|', 'Recall'.rjust(10), '|', 'Time'.rjust(10), '|', 'Eval'.rjust(10), '|', 'Eval proba'.rjust(10))
for model_name, model in classifiers.items():
    t0 = time.time()

    pipeline = get_pipeline(model, model_name)
    scoring = {'ROC AUC': 'roc_auc', 
               'Accuracy': 'accuracy', 
               'F1': 'f1', 
               'Precision': 'precision', 
               'Recall': 'recall'}
    results = cross_validate(pipeline, 
                             X_train, 
                             y_train, 
                             cv=cv, 
                             scoring=scoring, 
                             return_train_score=False, 
                             n_jobs=-1)
    
    results = pd.DataFrame(results)

    # fit on all train data and predict on test
    pipeline.fit(X_train, y_train)        
    y_pred = pipeline.predict(X_test)

    # check if the model has predict_proba method
    if hasattr(model, 'predict_proba'):
        y_pred_proba = pipeline.predict_proba(X_test)[:, 1]
    else:
        y_pred_proba = y_pred
        print('Model does not have proba method')

    # check if y_pred_proba has nan values
    if np.isnan(y_pred_proba).any():
        y_pred_proba = y_pred
    
    if not SUBMIT:
        score_eval = roc_auc_score(y_test, y_pred)
        score_eval_proba = roc_auc_score(y_test, y_pred_proba)
    else:
        score_eval = np.nan
        score_eval_proba = np.nan

    print(f'{model_name:30} | ' 
          f'{results["test_ROC AUC"].mean():10.4f} | ' 
          f'{results["test_ROC AUC"].std():10.4f} | '
          f'{results["test_Accuracy"].mean():10.4f} | '
          f'{results["test_F1"].mean():10.4f} | '
          f'{results["test_Precision"].mean():10.4f} | '
          f'{results["test_Recall"].mean():10.4f} | '
          f'{time.time() - t0:10.2f}s | '
          f'{score_eval:10.4f} | '
          f'{score_eval_proba:10.4f}'
          )

    # Save experiment results
    experiments[f'{model_name}_exp{exp_index}'] = (
        model_name, 
        exp_index, 
        pipeline, 
        results["test_ROC AUC"].mean(),
        results["test_ROC AUC"].std(),
        results["test_Accuracy"].mean(),
        results["test_F1"].mean(),
        results["test_Precision"].mean(),
        results["test_Recall"].mean(),
        time.time() - t0,
        score_eval)


Experiment 1: 6 models
Model name                     |    ROC AUC |    roc std |   Accuracy |         F1 |  Precision |     Recall |       Time |       Eval | Eval proba
LogisticRegression2            |     0.5000 |     0.0000 |     0.5578 |     0.0000 |     0.0000 |     0.0000 |       4.25s |        nan |        nan
GaussianNB                     |     0.7224 |     0.0873 |     0.6537 |     0.6165 |     0.6100 |     0.6454 |       0.49s |        nan |        nan
GaussianProcessClassifier      |     0.7331 |     0.0836 |     0.6738 |     0.6136 |     0.6494 |     0.5932 |       2.44s |        nan |        nan
BernoulliNB                    |     0.6028 |     0.0776 |     0.5931 |     0.4147 |     0.5448 |     0.4456 |       0.55s |        nan |        nan


In [101]:
now = time.strftime("%Y-%m-%d %H_%M_%S")
experiments_df = pd.DataFrame.from_dict(experiments, orient='index', columns=['model_name', 'exp_index', 'pipeline', 'mean', 'std', 'accuracy', 'f1', 'precision', 'recall', 'time', 'eval'])
experiments_df['mean-2std'] = experiments_df['mean'] - 2 * experiments_df['std']
experiments_df.to_excel(f'experiments/experiments_df_{now}.xlsx')
experiments_df.sort_values('mean-2std', ascending=False).head(30)

model_name  \
RandomForestClassifier_exp1                  RandomForestClassifier   
RandomForestClassifier_exp2                  RandomForestClassifier   
LogisticRegression_exp1                          LogisticRegression   
GaussianProcessClassifier_exp2            GaussianProcessClassifier   
CatBoostClassifier_exp2                          CatBoostClassifier   
SVC_exp2                                                        SVC   
LGBMClassifier_exp2                                  LGBMClassifier   
ExtraTreesClassifier_exp2                      ExtraTreesClassifier   
NuSVC_exp2                                                    NuSVC   
XGBClassifier1_exp19                                 XGBClassifier1   
XGBClassifier1_exp18                                 XGBClassifier1   
XGBClassifier2_exp18                                 XGBClassifier2   
XGBClassifier2_exp19                                 XGBClassifier2   
HistGradientBoostingClassifier_exp2  HistGradientBoostingClassifier   
GradientBoostingClassifier_exp2          GradientBoostingClassifier   
XGBClassifier_exp2                                    XGBClassifier   
BaggingClassifier_exp2                            BaggingClassifier   
LinearDiscriminantAnalysis_exp2          LinearDiscriminantAnalysis   
CalibratedClassifierCV_Ridge_exp2      CalibratedClassifierCV_Ridge   
CalibratedClassifierCV_LR_exp2            CalibratedClassifierCV_LR   
AdaBoostClassifier_exp1                          AdaBoostClassifier   
LogisticRegression_exp2                          LogisticRegression   
KNeighborsClassifier_exp1                      KNeighborsClassifier   
AdaBoostClassifier_exp2                          AdaBoostClassifier   
SVC_exp8                                                        SVC   
SVC_exp13                                                       SVC   
SVC_exp14                                                       SVC   
SVC_exp16                                                       SVC   
LogisticRegression_exp23                         LogisticRegression   
SVC_exp18                                                       SVC   

                                     exp_index  \
RandomForestClassifier_exp1                  1   
RandomForestClassifier_exp2                  2   
LogisticRegression_exp1                      1   
GaussianProcessClassifier_exp2               2   
CatBoostClassifier_exp2                      2   
SVC_exp2                                     2   
LGBMClassifier_exp2                          2   
ExtraTreesClassifier_exp2                    2   
NuSVC_exp2                                   2   
XGBClassifier1_exp19                        19   
XGBClassifier1_exp18                        18   
XGBClassifier2_exp18                        18   
XGBClassifier2_exp19                        19   
HistGradientBoostingClassifier_exp2          2   
GradientBoostingClassifier_exp2              2   
XGBClassifier_exp2                           2   
BaggingClassifier_exp2                       2   
LinearDiscriminantAnalysis_exp2              2   
CalibratedClassifierCV_Ridge_exp2            2   
CalibratedClassifierCV_LR_exp2               2   
AdaBoostClassifier_exp1                      1   
LogisticRegression_exp2                      2   
KNeighborsClassifier_exp1                    1   
AdaBoostClassifier_exp2                      2   
SVC_exp8                                     8   
SVC_exp13                                   13   
SVC_exp14                                   14   
SVC_exp16                                   16   
LogisticRegression_exp23                    23   
SVC_exp18                                   18   

                                                                              pipeline  \
RandomForestClassifier_exp1          (FeatureEngineering(level=1), PowerTransformer...   
RandomForestClassifier_exp2          (FeatureEngineering(level=1), PowerTransformer...   
LogisticRegression_exp1           

# SequentialFeatureSelector

In [10]:
# Evaluate performance of the models with sequential feature selection
from sklearn.feature_selection import SequentialFeatureSelector
from sklearn.model_selection import cross_val_score

set_config(transform_output="pandas")  # set to pandas

models = [
    # ('LogisticRegression', LogisticRegression(random_state=SEED, penalty='l1', solver='liblinear', max_iter=10000, C=0.02)),
    # ('SVC', SVC(probability=True, C=0.1, kernel='rbf', degree=4)),
    # ('LGBMClassifier', LGBMClassifier(boosting_type='gbdt', max_depth=1, learning_rate=0.33, random_state=SEED)),
    # ('XGBClassifier', XGBClassifier(booster='gbtree', max_depth=1, learning_rate=0.33, random_state=SEED)),
    # ('CatBoostClassifier', CatBoostClassifier(verbose=0, random_state=SEED, max_depth=1, learning_rate=0.33)),
    ('GaussianProcessClassifier', GaussianProcessClassifier(random_state=SEED)),
]

for model_name, model in models:
    for n in range(1, 6):
        X = X_train.copy()
        X = FeatureEngineering(level=1).fit_transform(X)
        X = PolynomialFeatures(degree=2, interaction_only=True).fit_transform(X)
        X = PowerTransformer().fit_transform(X)

        sfs = SequentialFeatureSelector(model, 
                                        n_features_to_select=n, 
                                        scoring='roc_auc', 
                                        cv=cv, 
                                        n_jobs=-1, 
                                        )
        X = sfs.fit_transform(X, y_train)

        scores = cross_val_score(model, X, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
        print(f'{model_name}: {scores.mean():.4f} +/- {scores.std():.4f}, features: {sfs.get_feature_names_out()}')

GaussianProcessClassifier: 0.8190 +/- 0.0627, features: ['ph calc']


KeyboardInterrupt: 

In [48]:
# Evaluate performance of the models with sequential feature selection
from sklearn.feature_selection import SequentialFeatureSelector
from sklearn.model_selection import cross_val_score

set_config(transform_output="pandas")  # set to pandas

models = [
    # ('KNN5', KNeighborsClassifier(n_neighbors=5)),
    # ('KNN10', KNeighborsClassifier(n_neighbors=10)),
    ('KNN15', KNeighborsClassifier(n_neighbors=15)),
    ('KNN20', KNeighborsClassifier(n_neighbors=20)),
    ('KNN25', KNeighborsClassifier(n_neighbors=25)),
    # ('KNN30', KNeighborsClassifier(n_neighbors=30)),
    # ('KNN35', KNeighborsClassifier(n_neighbors=35)),
    # ('KNN40', KNeighborsClassifier(n_neighbors=40)),
    # ('KNN45', KNeighborsClassifier(n_neighbors=45)),
    # ('KNN50', KNeighborsClassifier(n_neighbors=50)),
    # ('KNN100', KNeighborsClassifier(n_neighbors=100)),
]

for model_name, model in models:
    for n in range(1, 10):
        X = X_train.copy()
        X = FeatureEngineering(level=1).fit_transform(X)
        X = PolynomialFeatures(degree=2, interaction_only=True).fit_transform(X)
        X = PowerTransformer().fit_transform(X)

        sfs = SequentialFeatureSelector(model, 
                                        n_features_to_select=n, 
                                        scoring='roc_auc', 
                                        cv=cv, 
                                        n_jobs=-1, 
                                        )
        X = sfs.fit_transform(X, y_train)
        print(f'{model_name}: {sfs.get_feature_names_out()}')

        scores = cross_val_score(model, X, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
        print(f'{model_name}: {scores.mean():.4f} +/- {scores.std():.4f}')


KNN15: ['urea calcium_to_urea_ratio']
KNN15: 0.8066 +/- 0.0644
KNN15: ['ph ion_product' 'urea calcium_to_urea_ratio']
KNN15: 0.8144 +/- 0.0721
KNN15: ['gravity calc' 'ph ion_product' 'urea calcium_to_urea_ratio']
KNN15: 0.8180 +/- 0.0698
KNN15: ['gravity calc' 'ph ion_product' 'urea calcium_to_urea_ratio'
 'calc acidic']
KNN15: 0.8200 +/- 0.0681
KNN15: ['gravity calc' 'ph ion_product' 'urea calcium_to_urea_ratio'
 'calc acidic' 'ion_product calcium_to_urea_ratio']
KNN15: 0.8217 +/- 0.0677
KNN15: ['gravity calc' 'ph ion_product' 'urea calcium_to_urea_ratio'
 'calc ion_product' 'calc acidic' 'ion_product calcium_to_urea_ratio']
KNN15: 0.8218 +/- 0.0691
KNN15: ['calc' 'gravity calc' 'ph ion_product' 'urea calcium_to_urea_ratio'
 'calc ion_product' 'calc acidic' 'ion_product calcium_to_urea_ratio']
KNN15: 0.8236 +/- 0.0684
KNN15: ['1' 'calc' 'gravity calc' 'ph ion_product' 'urea calcium_to_urea_ratio'
 'calc ion_product' 'calc acidic' 'ion_product calcium_to_urea_ratio']
KNN15: 0.8236 +/- 

exception calling callback for <Future at 0x1b00fcbee20 state=finished raised PicklingError>
Traceback (most recent call last):
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\loky\backend\queues.py", line 153, in _feed
    obj_ = dumps(obj, reducers=reducers)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\loky\backend\reduction.py", line 271, in dumps
    dump(obj, buf, reducers=reducers, protocol=protocol)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\loky\backend\reduction.py", line 264, in dump
    _LokyPickler(file, reducers=reducers, protocol=protocol).dump(obj)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\cloudpickle\cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\parallel.py", line 268, in __reduce__
    self._reducer_callback()
  File "c:\U

KeyboardInterrupt: 

exception calling callback for <Future at 0x1b00f8d9700 state=finished raised PicklingError>
Traceback (most recent call last):
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\loky\backend\queues.py", line 153, in _feed
    obj_ = dumps(obj, reducers=reducers)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\loky\backend\reduction.py", line 271, in dumps
    dump(obj, buf, reducers=reducers, protocol=protocol)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\loky\backend\reduction.py", line 264, in dump
    _LokyPickler(file, reducers=reducers, protocol=protocol).dump(obj)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\cloudpickle\cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\parallel.py", line 268, in __reduce__
    self._reducer_callback()
  File "c:\U

exception calling callback for <Future at 0x1b00f8d9c40 state=finished raised PicklingError>
Traceback (most recent call last):
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\loky\backend\queues.py", line 153, in _feed
    obj_ = dumps(obj, reducers=reducers)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\loky\backend\reduction.py", line 271, in dumps
    dump(obj, buf, reducers=reducers, protocol=protocol)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\loky\backend\reduction.py", line 264, in dump
    _LokyPickler(file, reducers=reducers, protocol=protocol).dump(obj)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\externals\cloudpickle\cloudpickle_fast.py", line 602, in dump
    return Pickler.dump(self, obj)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\joblib\parallel.py", line 268, in __reduce__
    self._reducer_callback()
  File "c:\U

# Optuna

## GaussianProcessClassifier

In [8]:
set_config(transform_output="pandas")  # set to pandas
X = X_train.copy()
X = FeatureEngineering(level=1).fit_transform(X)
X = PolynomialFeatures(degree=2, interaction_only=True).fit_transform(X)
X = PowerTransformer().fit_transform(X)
X = X['ph calc']
def objective(trial):
    
    params = {
        'random_state': SEED,
        'kernel': trial.suggest_categorical('kernel', ['RBF', 'Matern', 'RationalQuadratic', 'ExpSineSquared']),
        'n_restarts_optimizer': trial.suggest_int('n_restarts_optimizer', 0, 10),
        'max_iter_predict': trial.suggest_int('max_iter_predict', 100, 1000),
        'warm_start': trial.suggest_categorical('warm_start', [True, False]),
        'copy_X_train': trial.suggest_categorical('copy_X_train', [True, False]),

             }
    model = GaussianProcessClassifier(**params)
    score = cross_val_score(model, X_train, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
    print(f'ROC AUC: {score.mean():.4f} +/- {score.std():.4f}')
    return score.mean() - 2 * score.std()

optuna.logging.set_verbosity(optuna.logging.INFO)
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=50)

df_study = study.trials_dataframe()
df_study.to_excel('study_GaussianProcess.xlsx')

study.best_params


[I 2023-04-17 16:37:07,082] A new study created in memory with name: no-name-b25590a0-c02f-4aec-9848-dd19e9ff4af1
[W 2023-04-17 16:37:10,953] Trial 0 failed because of the following error: ValueError('\nAll the 100 fits failed.\nIt is very likely that your model is misconfigured.\nYou can try to debug the error by setting error_score=\'raise\'.\n\nBelow are more details about the failures:\n--------------------------------------------------------------------------------\n100 fits failed with the following error:\nTraceback (most recent call last):\n  File "c:\\Users\\hzf04d\\Anaconda3\\envs\\MainEnv\\lib\\site-packages\\sklearn\\model_selection\\_validation.py", line 686, in _fit_and_score\n    estimator.fit(X_train, y_train, **fit_params)\n  File "c:\\Users\\hzf04d\\Anaconda3\\envs\\MainEnv\\lib\\site-packages\\sklearn\\gaussian_process\\_gpc.py", line 698, in fit\n    self._validate_params()\n  File "c:\\Users\\hzf04d\\Anaconda3\\envs\\MainEnv\\lib\\site-packages\\sklearn\\base.py", 

ValueError: 
All the 100 fits failed.
It is very likely that your model is misconfigured.
You can try to debug the error by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
100 fits failed with the following error:
Traceback (most recent call last):
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\sklearn\model_selection\_validation.py", line 686, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\sklearn\gaussian_process\_gpc.py", line 698, in fit
    self._validate_params()
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\sklearn\base.py", line 581, in _validate_params
    validate_parameter_constraints(
  File "c:\Users\hzf04d\Anaconda3\envs\MainEnv\lib\site-packages\sklearn\utils\_param_validation.py", line 97, in validate_parameter_constraints
    raise InvalidParam

## LGBMClassifier

In [116]:
def objective(trial):
    
    params = {
        'boosting_type': trial.suggest_categorical("boosting_type", ['gbdt', 'dart', 'goss']), # default=gbdt
        'num_leaves': trial.suggest_int("num_leaves", 7, 50), # default=31
        'max_depth' : trial.suggest_int("max_depth", 1, 8), # default=-1
        'learning_rate' : trial.suggest_float("learning_rate", 0.01, 0.5), # default=0.1
        'n_estimators' : trial.suggest_int("n_estimators", 50, 250), # default=100
        'min_child_weight' : trial.suggest_float("min_child_weight", 1e-4, 1e-2, log=True), # default=1e-3
        'colsample_bytree' : trial.suggest_float("colsample_bytree", 0.3, 1), # default=1.
        'random_state': SEED,
        # 'n_jobs' : -1,
             }
    model = LGBMClassifier(**params)
    score = cross_val_score(model, X, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
    print(f'ROC AUC: {score.mean():.4f} +/- {score.std():.4f}')
    return score.mean()

optuna.logging.set_verbosity(optuna.logging.INFO)
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=50)

df_study = study.trials_dataframe()
df_study.to_excel('study_LGBM.xlsx')

LGBM_params = study.best_params
LGBM_params

[I 2023-04-13 10:11:39,063] A new study created in memory with name: no-name-9977d674-cdd2-4512-8a36-a58b7f181b30
[I 2023-04-13 10:11:39,442] Trial 0 finished with value: 0.6666986759442031 and parameters: {'boosting_type': 'goss', 'num_leaves': 49, 'max_depth': 8, 'learning_rate': 0.05421398202647082, 'n_estimators': 127, 'min_child_weight': 0.00030166019449891023, 'colsample_bytree': 0.5637907887668816}. Best is trial 0 with value: 0.6666986759442031.


ROC AUC: 0.8032 +/- 0.0683


[I 2023-04-13 10:11:39,929] Trial 1 finished with value: 0.6035942275766748 and parameters: {'boosting_type': 'goss', 'num_leaves': 46, 'max_depth': 7, 'learning_rate': 0.4234822616215369, 'n_estimators': 205, 'min_child_weight': 0.0003678256013309526, 'colsample_bytree': 0.5202590709780883}. Best is trial 0 with value: 0.6666986759442031.


ROC AUC: 0.7414 +/- 0.0689


[I 2023-04-13 10:11:40,212] Trial 2 finished with value: 0.6453845890838694 and parameters: {'boosting_type': 'goss', 'num_leaves': 9, 'max_depth': 3, 'learning_rate': 0.1676807484261003, 'n_estimators': 108, 'min_child_weight': 0.001392469402560134, 'colsample_bytree': 0.4823441976760066}. Best is trial 0 with value: 0.6666986759442031.


...

[I 2023-04-13 10:14:00,732] Trial 498 finished with value: 0.683878452920895 and parameters: {'boosting_type': 'gbdt', 'num_leaves': 50, 'max_depth': 1, 'learning_rate': 0.41431746517496454, 'n_estimators': 67, 'min_child_weight': 0.0006053593826991208, 'colsample_bytree': 0.7063644661495002}. Best is trial 404 with value: 0.6902332427464182.


ROC AUC: 0.8144 +/- 0.0653


[I 2023-04-13 10:14:01,124] Trial 499 finished with value: 0.6392830688838168 and parameters: {'boosting_type': 'gbdt', 'num_leaves': 49, 'max_depth': 8, 'learning_rate': 0.4508155554471782, 'n_estimators': 76, 'min_child_weight': 0.0005299031245316652, 'colsample_bytree': 0.5186190424769502}. Best is trial 404 with value: 0.6902332427464182.


ROC AUC: 0.7764 +/- 0.0686


{'boosting_type': 'gbdt',
 'num_leaves': 46,
 'max_depth': 1,
 'learning_rate': 0.4304621639895126,
 'n_estimators': 76,
 'min_child_weight': 0.0003951963237213706,
 'colsample_bytree': 0.4399369092356428}

In [117]:
optuna.visualization.plot_optimization_history(study)

In [118]:
optuna.visualization.plot_param_importances(study)

In [119]:
optuna.visualization.plot_param_importances(
    study, target=lambda t: t.duration.total_seconds(), target_name="duration"
)

In [120]:
optuna.visualization.plot_slice(study)

## LogisticRegression

In [143]:
import optuna
X = X_train.copy()
# X = PolynomialFeatures(degree=2, include_bias=False).fit_transform(X)
X = PowerTransformer().fit_transform(X)
cv = RepeatedStratifiedKFold(n_repeats=20, n_splits=10, random_state=SEED)
def objective(trial):

    # solver_penalty = trial.suggest_categorical("solver_penalty", ['liblinear_l1', 'liblinear_l2', 
    #                                                               'saga_l1', 'saga_l2', 'saga_elasticnet', 'saga_none',
    #                                                               'newton-cg_l2', 'newton-cg_none',
    #                                                               'lbfgs_l2', 'lbfgs_none',
    #                                                               'sag_l2', 'sag_none',
    #                                                               'newton-cholesky_l2', 'newton-cholesky_none'])
    # 
    solver_penalty = trial.suggest_categorical("solver_penalty", ['liblinear_l1', 'saga_l1', 'saga_elasticnet'])                                                       
    
    params = {
        'solver': solver_penalty.split('_')[0], # default=lbfgs
        'penalty': solver_penalty.split('_')[1], # default=l2
        'C': trial.suggest_float("C", 1e-4, 1e4, log=True), # default=1.0
        # 'max_iter': trial.suggest_int("max_iter", 100, 1000), # default=100
        'random_state': SEED,
        'l1_ratio': trial.suggest_float("l1_ratio", 0, 1), # default=None
        # 'n_jobs' : -1,
        }

    if params['penalty'] != 'elasticnet':
        params['l1_ratio'] = None

    model = LogisticRegression(**params)
    score = cross_val_score(model, X, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
    print(f'ROC AUC: {score.mean():.4f} +/- {score.std():.4f}')
    return score.mean() - 2 * score.std()

optuna.logging.set_verbosity(optuna.logging.INFO)
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

df_study = study.trials_dataframe()
df_study.to_excel('study_LR.xlsx')

LGBM_params = study.best_params
LGBM_params

[I 2023-04-13 12:11:35,610] A new study created in memory with name: no-name-c157fbc5-d6b1-4a92-a627-fa0f80bb08fe
[I 2023-04-13 12:11:39,493] Trial 0 finished with value: 0.64289520157143 and parameters: {'solver_penalty': 'saga_elasticnet', 'C': 421.86351753667344, 'l1_ratio': 0.320252639986067}. Best is trial 0 with value: 0.64289520157143.


ROC AUC: 0.7853 +/- 0.0712


[I 2023-04-13 12:11:39,739] Trial 1 finished with value: 0.6430078287986086 and parameters: {'solver_penalty': 'saga_elasticnet', 'C': 0.1936630950092106, 'l1_ratio': 0.20549824379826442}. Best is trial 1 with value: 0.6430078287986086.


ROC AUC: 0.7855 +/- 0.0712


[I 2023-04-13 12:11:39,975] Trial 2 finished with value: 0.650751585063785 and parameters: {'solver_penalty': 'liblinear_l1', 'C': 0.08572553449676373, 'l1_ratio': 0.7405613215899222}. Best is trial 2 with value: 0.650751585063785.


...

[I 2023-04-13 12:13:30,644] Trial 498 finished with value: 0.6509327111055813 and parameters: {'solver_penalty': 'liblinear_l1', 'C': 0.058688053398573144, 'l1_ratio': 0.1931360988651356}. Best is trial 13 with value: 0.6511821366828551.


ROC AUC: 0.7901 +/- 0.0696


[I 2023-04-13 12:13:30,903] Trial 499 finished with value: 0.5 and parameters: {'solver_penalty': 'saga_l1', 'C': 0.000978951945651166, 'l1_ratio': 0.3299917457181094}. Best is trial 13 with value: 0.6511821366828551.


ROC AUC: 0.5000 +/- 0.0000


{'solver_penalty': 'liblinear_l1',
 'C': 0.02091787044510896,
 'l1_ratio': 0.6122157185321212}

In [144]:
optuna.visualization.plot_optimization_history(study)

In [145]:
optuna.visualization.plot_param_importances(study)

In [146]:
optuna.visualization.plot_slice(study)

## SVC

In [9]:
X = X_train.copy()
# X = PolynomialFeatures(degree=2, include_bias=False).fit_transform(X)
X = PowerTransformer().fit_transform(X)
# cv = RepeatedStratifiedKFold(n_repeats=20, n_splits=10, random_state=SEED)
def objective(trial):
    params = {
        'C': trial.suggest_float("C", 1e-4, 1e4, log=True), # default=1.0
        'kernel': trial.suggest_categorical("kernel", ['rbf', 'sigmoid']), # default=rbf
        'degree': trial.suggest_int("degree", 1, 5), # default=3
        # 'gamma': trial.suggest_float("gamma", 1e-4, 1e4, log=True), # default=scale
        # 'coef0': trial.suggest_float("coef0", 1e-4, 1e4, log=True), # default=0.0
        # 'shrinking': trial.suggest_categorical("shrinking", [True, False]), # default=True
        'probability': True,
        # 'tol': trial.suggest_float("tol", 1e-4, 1e-1, log=True), # default=1e-3
        # 'cache_size': trial.suggest_float("cache_size", 1e1, 1e4, log=True), # default=200
        # 'class_weight': trial.suggest_categorical("class_weight", [None, 'balanced']), # default=None
        # 'max_iter': trial.suggest_int("max_iter", 100, 1000), # default=-1
        # 'decision_function_shape': trial.suggest_categorical("decision_function_shape", ['ovo', 'ovr']), # default=ovr
        # 'break_ties': trial.suggest_categorical("break_ties", [True, False]), # default=False
        'random_state': SEED,
    }
    # print('kernel:', params['kernel'])
    print(params)
    model = SVC(**params)
    score = cross_val_score(model, X, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
    print(f'ROC AUC: {score.mean():.4f} +/- {score.std():.4f}')
    return score.mean() - 2 * score.std()

optuna.logging.set_verbosity(optuna.logging.INFO)
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=50)

df_study = study.trials_dataframe()
df_study.to_excel('study_SVC.xlsx')

study.best_params


[I 2023-04-17 13:35:38,446] A new study created in memory with name: no-name-d3d0dda9-1cbf-4f21-965f-fba121d7d1b6


{'C': 2130.1233064663884, 'kernel': 'sigmoid', 'degree': 2, 'probability': True, 'random_state': 15}


[I 2023-04-17 13:35:42,452] Trial 0 finished with value: 0.4953481007748276 and parameters: {'C': 2130.1233064663884, 'kernel': 'sigmoid', 'degree': 2}. Best is trial 0 with value: 0.4953481007748276.


ROC AUC: 0.6453 +/- 0.0750
{'C': 0.0020610707138744105, 'kernel': 'rbf', 'degree': 2, 'probability': True, 'random_state': 15}


[I 2023-04-17 13:35:43,334] Trial 1 finished with value: 0.6528735247141788 and parameters: {'C': 0.0020610707138744105, 'kernel': 'rbf', 'degree': 2}. Best is trial 1 with value: 0.6528735247141788.


...

[I 2023-04-17 13:36:22,102] Trial 48 finished with value: 0.6165092491140907 and parameters: {'C': 4.0179175219953205, 'kernel': 'rbf', 'degree': 5}. Best is trial 32 with value: 0.6633210733852621.


ROC AUC: 0.7776 +/- 0.0806
{'C': 0.8028768979471561, 'kernel': 'rbf', 'degree': 3, 'probability': True, 'random_state': 15}


[I 2023-04-17 13:36:22,829] Trial 49 finished with value: 0.6478346207242768 and parameters: {'C': 0.8028768979471561, 'kernel': 'rbf', 'degree': 3}. Best is trial 32 with value: 0.6633210733852621.


ROC AUC: 0.8012 +/- 0.0767


{'C': 0.11944540925257213, 'kernel': 'rbf', 'degree': 4}

In [10]:
optuna.visualization.plot_optimization_history(study)

In [11]:
optuna.visualization.plot_param_importances(study)

In [12]:
optuna.visualization.plot_slice(study)

## XGBoost

In [51]:
X = X_train.copy()
X = FeatureEngineering(level=1).fit_transform(X)
X = PolynomialFeatures(degree=2, include_bias=False).fit_transform(X)
X = X[['gravity', 'calc', 'osmo acidic']]

def objective(trial):
    
    params = {
        'n_estimators': trial.suggest_int("n_estimators", 100, 1000), # default=100
        'max_depth': trial.suggest_int("max_depth", 1, 10), # default=-1
        'learning_rate': trial.suggest_float("learning_rate", 1e-4, 1e-1, log=True), # default=0.1
        'subsample': trial.suggest_float("subsample", 0.1, 1), # default=1.0
        'colsample_bytree': trial.suggest_float("colsample_bytree", 0.1, 1), # default=1.0
             }
    model = XGBClassifier(**params)
    score = cross_val_score(model, X, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
    print(f'ROC AUC: {score.mean():.4f} +/- {score.std():.4f}')
    # return score.mean() - 2 * score.std()
    return score.mean()

optuna.logging.set_verbosity(optuna.logging.INFO)
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=500)

df_study = study.trials_dataframe()
df_study.to_excel('study_XGBoost.xlsx')

study.best_params

[I 2023-04-17 15:10:49,540] A new study created in memory with name: no-name-e6eb8883-05d0-4e61-afb7-f8594e524ca8
[I 2023-04-17 15:10:50,338] Trial 0 finished with value: 0.7979464285714285 and parameters: {'n_estimators': 193, 'max_depth': 10, 'learning_rate': 0.0004041996674980917, 'subsample': 0.7411370857106357, 'colsample_bytree': 0.4485733657569785}. Best is trial 0 with value: 0.7979464285714285.


ROC AUC: 0.7979 +/- 0.0702


[I 2023-04-17 15:10:53,088] Trial 1 finished with value: 0.8033826358826359 and parameters: {'n_estimators': 960, 'max_depth': 3, 'learning_rate': 0.0006978562305230485, 'subsample': 0.5290857048548289, 'colsample_bytree': 0.5718306463640136}. Best is trial 1 with value: 0.8033826358826359.


ROC AUC: 0.8034 +/- 0.0707


[I 2023-04-17 15:10:55,567] Trial 2 finished with value: 0.802452715934859 and parameters: {'n_estimators': 682, 'max_depth': 6, 'learning_rate': 0.00012084512561714093, 'subsample': 0.4883710080450191, 'colsample_bytree': 0.24870118004301167}. Best is trial 1 with value: 0.8033826358826359.


...

[I 2023-04-17 15:23:45,503] Trial 498 finished with value: 0.8286318542568543 and parameters: {'n_estimators': 571, 'max_depth': 1, 'learning_rate': 0.07248661985734026, 'subsample': 0.9992158816831058, 'colsample_bytree': 0.23602180195452746}. Best is trial 477 with value: 0.8289529650243935.


ROC AUC: 0.8286 +/- 0.0651


[I 2023-04-17 15:23:46,934] Trial 499 finished with value: 0.827636999244142 and parameters: {'n_estimators': 594, 'max_depth': 1, 'learning_rate': 0.07696081893916033, 'subsample': 0.9567606912735833, 'colsample_bytree': 0.2032314690968393}. Best is trial 477 with value: 0.8289529650243935.


ROC AUC: 0.8276 +/- 0.0651


{'n_estimators': 579,
 'max_depth': 1,
 'learning_rate': 0.06442086864191063,
 'subsample': 0.9998381832868174,
 'colsample_bytree': 0.2674808790429085}

In [55]:
study.best_params

{'n_estimators': 579,
 'max_depth': 1,
 'learning_rate': 0.06442086864191063,
 'subsample': 0.9998381832868174,
 'colsample_bytree': 0.2674808790429085}

In [52]:
optuna.visualization.plot_optimization_history(study)

In [53]:
optuna.visualization.plot_param_importances(study)

In [54]:
optuna.visualization.plot_slice(study)

# Test all features combinations

In [8]:
from sklearn.model_selection import cross_val_predict, RepeatedStratifiedKFold, StratifiedKFold
from itertools import combinations

set_config(transform_output="pandas")  # set to pandas

model = SVC(probability=True)
results = pd.DataFrame(columns=['combination', 'roc_auc', 'roc_auc_std'])

X_ = X_train.copy()
# X_ = PolynomialFeatures(degree=2, include_bias=False).fit_transform(X_)
X_ = FeatureEngineering(level=1).fit_transform(X_)
X_ = PowerTransformer().fit_transform(X_)

# List all possible combinations of features
features = X_.columns
combinations = [c for i in range(1, len(features)+1) for c in combinations(features, i)]

for combination in combinations:
    X = X_[list(combination)].copy()
    y_preds = []

    # Create a cross validation of 10 folds using predict_proba method
    for i in range(20):
        cv = StratifiedKFold(n_splits=10, random_state=SEED+i, shuffle=True)
        y_pred = cross_val_predict(model, X, y_train, cv=cv, method='predict_proba', n_jobs=-1)
        # print(f'ROC AUC: {roc_auc_score(y_train, y_pred[:, 1]):.4f}')
        y_preds.append(y_pred[:, 1])

    y_preds = np.array(y_preds)
    results = results.append({'combination': combination, 'roc_auc': roc_auc_score(y_train, y_preds.mean(axis=0)), 'roc_auc_std': y_preds.std(axis=0).mean()}, ignore_index=True)
    print(f'ROC AUC: {roc_auc_score(y_train, y_preds.mean(axis=0)):.4f} +/- {y_preds.std(axis=0).mean():.4f}, columns: {combination}')
    # print('-'*50)

ROC AUC: 0.6127 +/- 0.0162, columns: ('gravity',)
ROC AUC: 0.4039 +/- 0.0129, columns: ('ph',)
ROC AUC: 0.5749 +/- 0.0121, columns: ('osmo',)
ROC AUC: 0.5879 +/- 0.0317, columns: ('cond',)
ROC AUC: 0.6011 +/- 0.0150, columns: ('urea',)
ROC AUC: 0.7637 +/- 0.0160, columns: ('calc',)
ROC AUC: 0.7357 +/- 0.0116, columns: ('ion_product',)
ROC AUC: 0.6591 +/- 0.0095, columns: ('calcium_to_urea_ratio',)
ROC AUC: 0.5303 +/- 0.0081, columns: ('electrolyte_balance',)
ROC AUC: 0.5722 +/- 0.0127, columns: ('osmolality_to_sg_ratio',)
ROC AUC: 0.5731 +/- 0.0116, columns: ('osmo_density',)
ROC AUC: 0.4651 +/- 0.0008, columns: ('sangat acidic',)
ROC AUC: 0.4642 +/- 0.0021, columns: ('acidic',)
ROC AUC: 0.4938 +/- 0.0021, columns: ('neutral',)
ROC AUC: 0.4651 +/- 0.0008, columns: ('basic',)
ROC AUC: 0.4480 +/- 0.0126, columns: ('gravity', 'ph')
ROC AUC: 0.5687 +/- 0.0120, columns: ('gravity', 'osmo')
ROC AUC: 0.5904 +/- 0.0321, columns: ('gravity', 'cond')
ROC AUC: 0.6030 +/- 0.0147, columns: ('gravit

KeyboardInterrupt: 

# Search for constants multipliers for each feature

In [64]:
# multiply each feature by a constant and optimize the constants


def objective(trial):
    
    X = X_train.copy()
    # X = FeatureEngineering(level=1).fit_transform(X)
    # X = PolynomialFeatures(degree=2, include_bias=False).fit_transform(X)
    # X = PowerTransformer().fit_transform(X)
    features = X.columns
    constants = [trial.suggest_float(f'{feature}', 0, 10) for feature in features]
    X[features] = X[features] * constants
    
    # model = KNeighborsClassifier(n_neighbors=20, weights='distance', p=1, n_jobs=-1)
    model = LGBMClassifier(boosting_type='gbdt', max_depth=1, learning_rate=0.33, random_state=SEED)
    score = cross_val_score(model, X, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
    
    # return score.mean() - 2 * score.std()

    # Add L1 regularization
    L1 = sum([abs(constant) for constant in constants]) / len(constants)
    print(f'ROC AUC: {score.mean():.4f} +/- {score.std():.4f}, L1: {L1:.4f}')
    return score.mean() - 0.01 * L1

optuna.logging.set_verbosity(optuna.logging.INFO)
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

[I 2023-04-14 13:35:54,759] A new study created in memory with name: no-name-22fb76f7-458e-40c6-a5b6-ebbc6a06abcb
[I 2023-04-14 13:35:55,795] Trial 0 finished with value: 0.7558283984769979 and parameters: {'gravity': 8.386478916886961, 'ph': 7.826148286101111, 'osmo': 9.605899850391651, 'cond': 3.3100252528083063, 'urea': 4.534285822473066, 'calc': 6.58977775025356, 'ion_product': 2.8370981478080557, 'calcium_to_urea_ratio': 1.9263221069338443, 'electrolyte_balance': 0.386614802309464, 'osmolality_to_sg_ratio': 0.4990552996887043, 'osmo_density': 6.556975923369155, 'sangat acidic': 1.959418508738885, 'acidic': 1.0565547825280919, 'neutral': 1.0810779920340685, 'basic': 5.045337185134802, 'gravity^2': 0.7749733626917654, 'gravity ph': 5.486157985942274, 'gravity osmo': 5.754177729721581, 'gravity cond': 8.843774133536739, 'gravity urea': 6.3761663675083735, 'gravity calc': 3.150520417853678, 'gravity ion_product': 6.325379842423028, 'gravity calcium_to_urea_ratio': 5.263983450768846, '

ROC AUC: 0.8031 +/- 0.0684, L1: 4.7314


[I 2023-04-14 13:35:56,528] Trial 1 finished with value: 0.755158322507164 and parameters: {'gravity': 2.679207128942247, 'ph': 6.537836424694001, 'osmo': 9.072610080857974, 'cond': 3.4693763721315865, 'urea': 7.423153144919957, 'calc': 7.082905579457757, 'ion_product': 8.440795929098915, 'calcium_to_urea_ratio': 7.30222064421561, 'electrolyte_balance': 3.010212572227812, 'osmolality_to_sg_ratio': 1.5132503684213428, 'osmo_density': 9.525176616812166, 'sangat acidic': 4.67378087129655, 'acidic': 5.4622421053464425, 'neutral': 8.386250833805773, 'basic': 4.857859813810698, 'gravity^2': 7.1211977309848375, 'gravity ph': 3.975608751502233, 'gravity osmo': 7.19522679408461, 'gravity cond': 4.376678538733874, 'gravity urea': 3.5468090614002423, 'gravity calc': 1.8617872639079291, 'gravity ion_product': 2.095859350273528, 'gravity calcium_to_urea_ratio': 3.0394897697226253, 'gravity electrolyte_balance': 7.002429071136679, 'gravity osmolality_to_sg_ratio': 3.424684585191585, 'gravity osmo_de

ROC AUC: 0.8032 +/- 0.0684, L1: 4.8052


[I 2023-04-14 13:35:57,250] Trial 2 finished with value: 0.7485943948984953 and parameters: {'gravity': 4.713994978174801, 'ph': 4.87995781387864, 'osmo': 9.381393227117158, 'cond': 1.8189055816812216, 'urea': 4.9980868644204035, 'calc': 3.487656765183853, 'ion_product': 6.9434808909578045, 'calcium_to_urea_ratio': 7.76034336487125, 'electrolyte_balance': 6.271950936838632, 'osmolality_to_sg_ratio': 7.642440706386967, 'osmo_density': 4.425472171304261, 'sangat acidic': 7.5975574733505455, 'acidic': 2.2688995122647695, 'neutral': 9.174951681046116, 'basic': 4.7485861117022825, 'gravity^2': 3.2338400422353497, 'gravity ph': 5.910715830197986, 'gravity osmo': 2.501602632596056, 'gravity cond': 9.488417896700632, 'gravity urea': 5.623702322668538, 'gravity calc': 8.062576937693093, 'gravity ion_product': 8.898715810314354, 'gravity calcium_to_urea_ratio': 9.18017883130352, 'gravity electrolyte_balance': 2.8295910605499386, 'gravity osmolality_to_sg_ratio': 9.724893928413124, 'gravity osmo_

...

ROC AUC: 0.8032 +/- 0.0684, L1: 3.9695


[I 2023-04-14 13:38:42,894] Trial 198 finished with value: 0.7630497820222761 and parameters: {'gravity': 5.845997994906763, 'ph': 7.277407411494449, 'osmo': 0.11211215293783552, 'cond': 0.8409301143910785, 'urea': 5.148880428655718, 'calc': 0.528952026336302, 'ion_product': 0.20100060578825235, 'calcium_to_urea_ratio': 0.7048637069396819, 'electrolyte_balance': 0.7012481346614543, 'osmolality_to_sg_ratio': 1.5459054921421296, 'osmo_density': 8.903037864902364, 'sangat acidic': 0.0020782617433503653, 'acidic': 9.97869688848526, 'neutral': 8.335346182521219, 'basic': 7.3413931068864695, 'gravity^2': 1.8942991920644245, 'gravity ph': 7.883767463058139, 'gravity osmo': 5.629263459182323, 'gravity cond': 0.42363892647215495, 'gravity urea': 8.50385703076586, 'gravity calc': 9.804364009072442, 'gravity ion_product': 0.9739100830741885, 'gravity calcium_to_urea_ratio': 1.54579160057677, 'gravity electrolyte_balance': 0.7483936910585018, 'gravity osmolality_to_sg_ratio': 0.5947960867828065, '

ROC AUC: 0.8033 +/- 0.0680, L1: 4.0295


[I 2023-04-14 13:38:43,838] Trial 199 finished with value: 0.7631858314009927 and parameters: {'gravity': 5.6409347401239645, 'ph': 7.427393786806707, 'osmo': 0.13766539475624812, 'cond': 0.8952504760823148, 'urea': 4.76494078497008, 'calc': 1.5158334965345601, 'ion_product': 0.0009391472761288155, 'calcium_to_urea_ratio': 0.7515260455106444, 'electrolyte_balance': 0.6646422584965318, 'osmolality_to_sg_ratio': 1.6235045656588334, 'osmo_density': 8.91141038430821, 'sangat acidic': 0.14936228554515374, 'acidic': 9.966213556213994, 'neutral': 8.355957661912074, 'basic': 7.460201496135335, 'gravity^2': 1.8712318292280226, 'gravity ph': 7.882204289864735, 'gravity osmo': 5.576417334490168, 'gravity cond': 0.4772399388746531, 'gravity urea': 8.835120699158438, 'gravity calc': 9.722172478510707, 'gravity ion_product': 1.03765644881576, 'gravity calcium_to_urea_ratio': 1.5596245214147366, 'gravity electrolyte_balance': 0.6757870643896984, 'gravity osmolality_to_sg_ratio': 0.5975729295073338, '

ROC AUC: 0.8031 +/- 0.0684, L1: 3.9957


In [65]:
study.best_params

{'gravity': 5.314056772612017,
 'ph': 7.33772607200785,
 'osmo': 0.22420740740978168,
 'cond': 0.842700633520348,
 'urea': 3.522219309117736,
 'calc': 0.6072554014217533,
 'ion_product': 0.34825986732111436,
 'calcium_to_urea_ratio': 0.753472417881864,
 'electrolyte_balance': 0.6075509570212895,
 'osmolality_to_sg_ratio': 1.5683614719644832,
 'osmo_density': 8.540040723222967,
 'sangat acidic': 0.6846000799658752,
 'acidic': 9.363344008737853,
 'neutral': 8.35642972050837,
 'basic': 7.05954591701058,
 'gravity^2': 1.51722816202649,
 'gravity ph': 7.5827525445781685,
 'gravity osmo': 6.036109744728954,
 'gravity cond': 0.45637675271505296,
 'gravity urea': 8.42698476796797,
 'gravity calc': 9.727029343981165,
 'gravity ion_product': 1.0127834681433692,
 'gravity calcium_to_urea_ratio': 1.474444692660102,
 'gravity electrolyte_balance': 0.36350221942667704,
 'gravity osmolality_to_sg_ratio': 0.7067130182042457,
 'gravity osmo_density': 1.4621108401959897,
 'gravity sangat acidic': 2.0517

In [66]:
optuna.visualization.plot_optimization_history(study)

In [67]:
optuna.visualization.plot_param_importances(study)

In [68]:
optuna.visualization.plot_slice(study)

In [52]:
LR = LogisticRegression(random_state=SEED, penalty='l1', solver='liblinear', max_iter=10000, C=0.02)
scores = cross_val_score(LR, X_train, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
print(f'ROC AUC: {scores.mean():.4f} +/- {scores.std():.4f}')

LR.fit(X_train, y_train)
LR.coef_

ROC AUC: 0.7825 +/- 0.0767


array([[ 0.        , -0.14446138, -0.00101929, -0.00785747,  0.00150155,
         0.27377441]])

In [51]:
X_train.columns

Index(['gravity', 'ph', 'osmo', 'cond', 'urea', 'calc'], dtype='object')

# Stack models

In [65]:
# Stacking ensemble
from sklearn.ensemble import StackingClassifier
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline

from mlxtend.classifier import StackingCVClassifier

set_config(transform_output="pandas")  # set to pandas

cv = RepeatedStratifiedKFold(n_splits=10, n_repeats=10, random_state=SEED)

estimators = [
    make_pipeline(
        FeatureSelector(feature_names=['ph calc']),
        PowerTransformer(), 
        LogisticRegression(random_state=SEED, penalty='l1', solver='liblinear', max_iter=10000, C=0.02)
    ),
    make_pipeline(
        FeatureSelector(feature_names=['calc', 'gravity calc', 'ph ion_product', 'urea calcium_to_urea_ratio', 'calc ion_product', 'calc acidic', 'ion_product calcium_to_urea_ratio']),
        PowerTransformer(),
        KNeighborsClassifier(n_neighbors=15)
    ),
    make_pipeline(
        FeatureSelector(feature_names=['ph calc', 'cond urea']),
        PowerTransformer(),
        SVC(probability=True, C=0.1, kernel='rbf', degree=4)
    ),
    make_pipeline(    
        FeatureSelector(feature_names=['gravity', 'calc', 'osmo acidic']),
        LGBMClassifier(boosting_type='gbdt', max_depth=1, learning_rate=0.33, random_state=SEED)
    ),
    make_pipeline(
        FeatureSelector(feature_names=['gravity', 'calc', 'osmo acidic']),
        XGBClassifier(booster='gbtree', max_depth=1, learning_rate=0.065, n_estimators=500, col_sample_bytree=0.25, random_state=SEED)
    ),
    make_pipeline(
        FeatureSelector(feature_names=['ph calc']),
        PowerTransformer(),
        GaussianProcessClassifier(random_state=SEED),
    )
]

# Data preprocessing
X = X_train.copy()
X = FeatureEngineering(level=1).fit_transform(X)
X = PolynomialFeatures(degree=2, interaction_only=True).fit_transform(X)

# Eval each model performance
for estimator in estimators:
    scores = cross_val_score(estimator, X, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
    print(f'Model: {estimator[-1]}, ROC AUC: {scores.mean():.4f} +/- {scores.std():.4f}')

# Stacking ensemble
stacking = StackingCVClassifier(classifiers=estimators, 
                                meta_classifier=RidgeClassifierCV(alphas=np.logspace(-3, 3, 10), cv=5, scoring='roc_auc'),
                                cv=StratifiedKFold(n_splits=20, random_state=SEED, shuffle=True), 
                                use_probas=True, 
                                use_features_in_secondary=False, 
                                random_state=SEED
)
    
scores = cross_val_score(stacking, X, y_train, cv=cv, scoring='roc_auc', n_jobs=-1)
print(f'Stacking ROC AUC: {scores.mean():.4f} +/- {scores.std():.4f}')

Model: LogisticRegression(C=0.02, max_iter=10000, penalty='l1', random_state=15,
                   solver='liblinear'), ROC AUC: 0.7936 +/- 0.0717
Model: KNeighborsClassifier(n_neighbors=15), ROC AUC: 0.8232 +/- 0.0688
Model: SVC(C=0.1, degree=4, probability=True), ROC AUC: 0.8243 +/- 0.0628
Model: LGBMClassifier(learning_rate=0.33, max_depth=1, random_state=15), ROC AUC: 0.8274 +/- 0.0648
Model: XGBClassifier(base_score=None, booster='gbtree', callbacks=None,
              col_sample_bytree=0.25, colsample_bylevel=None,
              colsample_bynode=None, colsample_bytree=None,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, feature_types=None, gamma=None, gpu_id=None,
              grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.065, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=1, max_leaves=None,
       

In [62]:
X_test_for_stacking = X_test.copy()
X_test_for_stacking = FeatureEngineering(level=1).fit_transform(X_test_for_stacking)
X_test_for_stacking = PolynomialFeatures(degree=2, interaction_only=True).fit_transform(X_test_for_stacking)

y_pred = stacking.fit(X, y_train).predict_proba(X_test_for_stacking)[:, 1]

[15:34:50] WARNING: C:\Users\dev-admin\croot2\xgboost-split_1675461376218\work\src\learner.cc:767: 
Parameters: { "col_sample_bytree" } are not used.

[15:34:50] WARNING: C:\Users\dev-admin\croot2\xgboost-split_1675461376218\work\src\learner.cc:767: 
Parameters: { "col_sample_bytree" } are not used.

[15:34:50] WARNING: C:\Users\dev-admin\croot2\xgboost-split_1675461376218\work\src\learner.cc:767: 
Parameters: { "col_sample_bytree" } are not used.

[15:34:50] WARNING: C:\Users\dev-admin\croot2\xgboost-split_1675461376218\work\src\learner.cc:767: 
Parameters: { "col_sample_bytree" } are not used.

[15:34:50] WARNING: C:\Users\dev-admin\croot2\xgboost-split_1675461376218\work\src\learner.cc:767: 
Parameters: { "col_sample_bytree" } are not used.

[15:34:50] WARNING: C:\Users\dev-admin\croot2\xgboost-split_1675461376218\work\src\learner.cc:767: 
Parameters: { "col_sample_bytree" } are not used.

[15:34:51] WARNING: C:\Users\dev-admin\croot2\xgboost-split_1675461376218\work\src\learner.cc:

# Submission

In [63]:
sub = pd.read_csv('submissions/sample_submission.csv')
sub[TARGET] = y_pred
now = time.strftime("%Y-%m-%d %H_%M_%S")
sub.to_csv(f'submissions/submission_StackingLR_{now}.csv', index=False)